<h1 align="center"> 
Predicting the Cause of Wildfires 
</h1> 
<h2 align="center"> 
DATS 6501_10, Spring 2019, Capstone Project ( Visualization )
</h2>

<h4 align="center"> 
Author: Jiajun Wu
</h4>

In [1]:
import sqlite3
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings("ignore")

In [2]:
#Load the data 
sqlite_file = "FPA_FOD_20170508.sqlite"
conn=sqlite3.connect(sqlite_file)
c = conn.cursor()
fires = pd.read_sql_query("SELECT * FROM fires", conn)

In [3]:
#Julian Date format to Gregorian dates
fires['DATE'] = pd.to_datetime(fires['DISCOVERY_DATE'] - pd.Timestamp(0).to_julian_date(), unit='D')
fires['MONTH'] = pd.DatetimeIndex(fires['DATE']).month
fires['DAY_OF_WEEK'] = fires['DATE'].dt.weekday_name

In [4]:
#Select necessary columns 
df = fires[['STAT_CAUSE_DESCR','DATE','FIRE_YEAR','LATITUDE','LONGITUDE','FIRE_SIZE','DISCOVERY_DATE','MONTH','DAY_OF_WEEK','STATE']]
#Clean the Data
df.replace('?', np.NaN, inplace=True)
df.dropna(how='any', inplace=True)
print('Number of rows after removing rows with missing values: ' + str(df.shape[0]))

Number of rows after removing rows with missing values: 1880465


In [ ]:
#fires.to_csv("Cleaned_fires.csv")

In [ ]:
#fires.head(10)

In [ ]:
#fires.columns

# Geographic Heatmap 

Folium builds on the data wrangling strengths of the Python ecosystem and the mapping strengths of the Leaflet.js library. Manipulate your data in Python, then visualize it in on a Leaflet map via Folium.

In [5]:
import geopandas as gpd
# terminal: pip install folium
# then, terminal: jupyter notebook
import folium 
from folium.plugins import HeatMap

In [ ]:
# fires.shape
# (1880465, 42)

## Heatmap With Fire by Size 1992 - 2015

In [6]:
num1 = 1880465
lat1 = np.array(fires["LATITUDE"][0:num1])                       
lon1 = np.array(fires["LONGITUDE"][0:num1]) 
firesize = np.array(fires["FIRE_SIZE"][0:num1],dtype=float)
data1 = [[lat1[i],lon1[i],firesize[i]] for i in range(num1)] 
#data1

In [7]:
# http://blog.yeshuanova.com/post/2017/10/python-visulization-folium/
from folium.plugins import HeatMap
# tiles= Stamen Terrain,Stamen Toner,Mapbox Bright,Mapbox Control Room
m1 = folium.Map(location=[42.5, -75.5], zoom_start=7)
HeatMap(data1).add_to(m1)
# Make sure to open the heatmap through Chrome (takes 15 mins, because the data is  huge),
# and Safari will take forever. 
file_path = r"test1.html"
m1.save(file_path)  # save as html

# HeatMap With Time Plugin (Arson)

We can also animate our heat maps to change the data being shown on it based on certain dimension(s) (i.e. hour, month) using a class method called HeatMapWithTime(). This method will allow us to animate the heat map that is rendered by our notebook.
https://towardsdatascience.com/data-101s-spatial-visualizations-and-analysis-in-python-with-folium-39730da2adf


In [8]:
# https://nbviewer.jupyter.org/github/python-visualization/folium/blob/master/examples/HeatMapWithTime.ipynb
# https://altran-data-analytics.netlify.com/2018/04/23/ukaccidents/
# https://python-forum.io/Thread-Folium-HeatMapWithTime-is-not-displaying-data-point
# import folium.plugins as plugins
from folium.plugins import HeatMapWithTime
from datetime import datetime, timedelta
#import cartopy.crs as ccrs


In [9]:
# select london area (around Big Ben)
from folium import plugins
m2 = folium.Map(location=[42.5, -75.5], zoom_start=13) 

heat_df = fires.loc[fires['STAT_CAUSE_DESCR']=='Arson'].copy()

# Create weight column, using date

years = heat_df['FIRE_YEAR']
years = [float(i) for i in years]
years = np.array(years)
weights = years

unique_weights = np.unique(weights)
hmap_weights = unique_weights[0::1]

heat_df['Weight'] = weights
heat_df['Weight'] = heat_df['Weight'].astype(float)
heat_df = heat_df.dropna(axis=0, subset=['LATITUDE', 'LONGITUDE', 'Weight'])

# List comprehension to create list of lists
heat_data = [[[row['LATITUDE'], row['LONGITUDE']] 
              for index, row in heat_df[heat_df['Weight'] == i].iterrows()] 
             for i in hmap_weights]
# Plot it on the map
hm = plugins.HeatMapWithTime(heat_data, auto_play=True, max_opacity=0.8, radius = 20)
hm.add_to(m2)
# Display the map
m2